In [1]:
import tensorflow as tf
import numpy as np 
from sklearn.datasets import fetch_california_housing
from sklearn import linear_model
from sklearn.cross_validation import train_test_split
from IPython.display import clear_output, Image, display, HTML
from __future__ import print_function

def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = "<stripped %d bytes>"%size
    return strip_def

def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = graph_def
    #strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))

    iframe = """
        <iframe seamless style="width:1200px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))
###### Implement Data Preprocess here ######
tf.reset_default_graph()
dataset = fetch_california_housing(data_home='./')
dataset.data -= np.mean(dataset.data, axis=0)
dataset.data /= np.std(dataset.data, axis=0)

###### End Data Preprocess ######
#training portion
tr_portion = 0.9
total_size = dataset.data.shape[0]
tr_size = int(total_size* tr_portion)
dataset.target=dataset.target.reshape([total_size, 1])

Ytr = dataset.target[0:tr_size,[0]]
# ###### Start TF session ######

#create 20640*9 ones array
Xtr = np.ones([tr_size,9])
Xtr[:,1:9] = dataset.data[0:tr_size,:]


X = tf.constant(Xtr,name = 'X')

Y = tf.constant(Ytr,name = 'Y')

XX = tf.matmul(tf.transpose(X),X,name = 'XX')

inv_XX = tf.matrix_inverse(XX,name = 'inv_XX')

XY = tf.matmul(tf.transpose(X),Y,name='XY')

output = tf.matmul(inv_XX,XY,name = 'output')
    

# Initialize the variables (i.e. assign their default value)
init = tf.global_variables_initializer() 

###### Start TF session ######
with tf.Session() as sess:
    # Run the initializer
    sess.run(init)
    show_graph(tf.get_default_graph().as_graph_def())
    
    #W[0]=bias , W[1:9]=weights 
    W = sess.run(output)
    print('b=',W[0],'\nW=',W[1:9])
    
    #calculate testing set error
    t=0
    for i in range(tr_size,total_size):
        t = t+np.abs(np.matmul(dataset.data[i],W[1:9])+W[0]-dataset.target[i])
    print('error rate:',t/(total_size-tr_size))

#Explanation of graph
#cell init: the essential component for running the session
#cell X:size=20640*9,the first col is ones and the reset are 8 input features)
#cell Y:data target Y(size = 20640*1)
#cell XX: matrix multiply of input X array and the transpose of itself, e.g.XX = X'X 
#cell inv_XX: matrix inverse of cell XX
#cell XY: matrix multiply of input X array and data target Y
#cell output: The linear regression formula,e.g. inv(X'X)*XY

E:\Anaconda\lib\site-packages\sklearn\cross_validation.py:41: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


b= [ 2.07721356] 
W= [[ 0.84053841]
 [ 0.12394536]
 [-0.28168942]
 [ 0.3227816 ]
 [-0.00191843]
 [-0.0583528 ]
 [-0.92267477]
 [-0.89473748]]
error rate: [ 0.435447]
